In [102]:
import os
import os
import json
from llama_index.core import SimpleDirectoryReader
import ollama
from groq import Groq
from langchain import PromptTemplate
# from langchain.chat_models import ChatOpenAI
from langchain.chains.summarize import load_summarize_chain
from langchain.text_splitter import RecursiveCharacterTextSplitter
from PyPDF2 import PdfReader
from langchain.docstore.document import Document
from langchain_community.vectorstores import FAISS
from path import Path
from langchain_google_genai import ChatGoogleGenerativeAI
from langchain_core.output_parsers import StrOutputParser
from langchain_core.runnables import RunnablePassthrough
import pickle
import time

In [103]:
!pip install faiss-cpu
import faiss

I0000 00:00:1728296958.367431   18369 fork_posix.cc:77] Other threads are currently calling into gRPC, skipping fork() handlers


In [104]:
#Importiong api keys
GROQ_API_KEY = os.getenv("GROQ_API_KEY")
GEMINI_API_KEY = os.getenv("GEMINI_API")

In [105]:
Parent_directory = Path('/run/media/aasiku/Vault/Aarush/Papers')
File_paths = Path.glob(Parent_directory, '*.pdf')

### Summarization

In [106]:
# Reading the pdf file
Filepath = File_paths[0]
pdfreader = PdfReader(Filepath)
text = ''
for i, page in enumerate(pdfreader.pages):
    content = page.extract_text()
    if content:
        text += content

#### Prompts for summarizing

In [34]:
chunks_prompt="""
Sumarise the bellow document, it will be used to later match the document with a user query, so capture the most important informations.
Document:`{text}'.Also in a line return the keywords in the document, these keywords must include the vast majority of the important points in the document.Use the maximum number of characters to express the summary under 20,000 characters.
Summary:
"""
map_prompt_template=PromptTemplate(input_variables=['text'],
                                    template=chunks_prompt)

In [35]:
final_combine_prompt='''
Provide a final summary of the entire document with these important points, this will be used to match the document with a user query, so capture the most important informations.Also in a line return the keywords in the document, these keywords must include the vast majority of the important points in the document.Use the maximum number of characters to express the summary under 20,000 characters.
Document: `{text}`
'''
final_combine_prompt_template=PromptTemplate(input_variables=['text'],
                                             template=final_combine_prompt)

In [43]:
## Splittting the text
text_splitter = RecursiveCharacterTextSplitter(chunk_size=300000, chunk_overlap=200) # 300k characters per chunk, or nearly 75,000 tokens

chunks = text_splitter.create_documents([text])

In [44]:
len(chunks) # Checking the length of the chunks so that it does not exceed the limit of 1 million tokens

8

In [48]:
split_chunks = []
for x in range(0,len(chunks),12):
    split_chunks.append([chunks[x:x+12]])

In [49]:
len(split_chunks)

1

In [50]:
split_chunks

[[Document(metadata={}, page_content='In Praise of Computer Organization and Design: The Hardware/\nSoftware Interface , Fifth Edition   \n “Textbook selection is oft  en a frustrating act of compromise—pedagogy, content \ncoverage, quality of exposition, level of rigor, cost.  Computer Organization and \nDesign   is the rare book that hits all the right notes across the board, without \ncompromise. It is not only the premier computer organization textbook, it is a \nshining example of what all computer science textbooks could and should be. ”\n  —Michael Goldweber,  Xavier University     \n “I have been using  Computer Organization and Design   for years, from the very \nfi rst edition. Th  e new Fift  h Edition is yet another outstanding improvement on an \nalready classic text. Th  e evolution from desktop computing to mobile computing \nto Big Data brings new coverage of embedded processors such as the ARM, new material on how soft  ware and hardware interact to increase performanc

In [110]:

#! Run this cell 
# Functionizing till split_chunks
def input_llm_pdf(File_path):
    # Reading the pdf file
    pdfreader = PdfReader(File_path)
    text = ''
    for i, page in enumerate(pdfreader.pages):
        content = page.extract_text()
        if content:
            text += content
    # Converting the text of the pdf of Document object
    docs = [Document(page_content=text)]
    docs
    ## Splittting the text
    text_splitter = RecursiveCharacterTextSplitter(chunk_size=300000, chunk_overlap=200) # 300k characters per chunk, or nearly 75,000 tokens
    chunks = text_splitter.create_documents([text])
    split_chunks = []
    for x in range(0,len(chunks),12):
        split_chunks.append([chunks[x:x+12]])
    return split_chunks

In [111]:
# Using langsmith to monitor the progress of the summarization
if os.environ.get("LANGCHAIN_API")!="":
    os.environ["LANGCHAIN_TRACING_V2"] = "true"
    os.environ["LANGCHAIN_API_KEY"]=os.environ.get("LANGCHAIN_API")
    os.environ["LANGCHAIN_ENDPOINT"]="https://api.smith.langchain.com"
    os.environ["LANGCHAIN_PROJECT"]="LearnLang"

In [112]:
from langchain_google_genai import ChatGoogleGenerativeAI
GEMINI_API_KEY=os.environ.get("GEMINI_API")
llm = ChatGoogleGenerativeAI(model="gemini-1.5-flash",api_key=GEMINI_API_KEY)

In [113]:
summary_chain = load_summarize_chain(
    llm=llm,
    chain_type='map_reduce',
    map_prompt=map_prompt_template,
    combine_prompt=final_combine_prompt_template,
    verbose=True
)


In [54]:
start_time = time.time()
endtime = None
output = ''
for file_path in File_paths:
    split_chunks = input_llm_pdf(file_path)
    for chunks in split_chunks:
        start_time = time.time()
        output += summary_chain.run(chunks)
        endtime = time.time()
        if (endtime - start_time) < 60:
            time.sleep(60 - (endtime - start_time))
    output_doc = Document(page_content=output)
    chunks = text_splitter.create_documents([output])
    final_summary = summary_chain.run(chunks)

/tmp/ipykernel_18369/3006975453.py:6: LangChainDeprecationWarning: The method `Chain.run` was deprecated in langchain 0.1.0 and will be removed in 1.0. Use :meth:`~invoke` instead.
  output += summary_chain.run(chunks)




> Entering new MapReduceDocumentsChain chain...


> Entering new LLMChain chain...
Prompt after formatting:

Sumarise the bellow document, it will be used to later match the document with a user query, so capture the most important informations.
Document:`In Praise of Computer Organization and Design: The Hardware/
Software Interface , Fifth Edition   
 “Textbook selection is oft  en a frustrating act of compromise—pedagogy, content 
coverage, quality of exposition, level of rigor, cost.  Computer Organization and 
Design   is the rare book that hits all the right notes across the board, without 
compromise. It is not only the premier computer organization textbook, it is a 
shining example of what all computer science textbooks could and should be. ”
  —Michael Goldweber,  Xavier University     
 “I have been using  Computer Organization and Design   for years, from the very 
fi rst edition. Th  e new Fift  h Edition is yet another outstanding improvement on an 
already classic text

In [55]:
output_doc = Document(page_content=output)
chunks = text_splitter.create_documents([output])
final_summary = summary_chain.run(chunks)



> Entering new MapReduceDocumentsChain chain...


> Entering new LLMChain chain...
Prompt after formatting:

Sumarise the bellow document, it will be used to later match the document with a user query, so capture the most important informations.
Document:`This document provides a comprehensive overview of computer organization and design, covering key concepts and advancements in hardware and software. It focuses on the interaction between hardware and software, particularly in the context of the PostPC era dominated by mobile devices and cloud computing. The book explores various aspects of computer architecture, including instruction set architecture, memory hierarchy, parallel processing, and assembly language. It emphasizes the importance of performance and energy efficiency, highlighting key techniques for optimizing these aspects. The document also delves into the concepts of virtual machines and virtual memory, explaining how they contribute to efficient resource management an

In [116]:
final_summary = f"File_path: {File_paths[0]} \n"+final_summary

In [118]:
final_summary 

'File_path /run/media/aasiku/Vault/Aarush/Papers/Attention_is_all_you_need.pdf \nThis document provides a comprehensive overview of computer organization and design, focusing on the interplay between hardware and software in the context of the PostPC era, characterized by mobile devices and cloud computing. It explores key aspects of computer architecture, including instruction set architecture, memory hierarchy, and parallel processing, with an emphasis on performance and energy efficiency. The document also delves into virtual machines and virtual memory, explaining their roles in efficient resource management. \n\nKey concepts covered include instruction set architecture (ISA), memory hierarchy (cache, multilevel cache), parallel processing (pipelining, multiprocessor, GPU), I/O (DMA, interrupt), assembly language, compilers and assemblers, operating systems (virtual machines, virtual memory), performance optimization, energy efficiency, reliability and dependability, and key concep

In [114]:
output_doc

Document(metadata={'File_path': 'ComputerOrganisation.pdf'}, page_content="This document provides a comprehensive overview of computer organization and design, covering key concepts and advancements in hardware and software. It focuses on the interaction between hardware and software, particularly in the context of the PostPC era dominated by mobile devices and cloud computing. The book explores various aspects of computer architecture, including instruction set architecture, memory hierarchy, parallel processing, and assembly language. It emphasizes the importance of performance and energy efficiency, highlighting key techniques for optimizing these aspects. The document also delves into the concepts of virtual machines and virtual memory, explaining how they contribute to efficient resource management and memory utilization. \n\nKeywords: Computer Organization, Computer Architecture, Hardware, Software, PostPC Era, Mobile Devices, Cloud Computing, Performance, Energy Efficiency, Inst

### RAG PIPEPLINE

In [59]:
from langchain_google_genai import GoogleGenerativeAIEmbeddings
embeddings = GoogleGenerativeAIEmbeddings(model="models/text-embedding-004",google_api_key=GEMINI_API_KEY)

In [60]:
text_splitter = RecursiveCharacterTextSplitter(chunk_size=5000, chunk_overlap=200)
chunks = text_splitter.create_documents([text])

In [61]:
len(chunks)

485

In [63]:
split_chunks = []
for x in range(0,len(chunks), 1400):
    split_chunks.append(chunks[x:x+1400])

In [65]:
len(split_chunks)

1

In [68]:
!mkdir VectorDatabases

mkdir: cannot create directory ‘VectorDatabases’: File exists


I0000 00:00:1728295390.677494   18369 fork_posix.cc:77] Other threads are currently calling into gRPC, skipping fork() handlers


In [92]:
path_vector_db_folder = Path.joinpath("VectorDatabases",File_path)
path_vector_db = Path.joinpath(path_vector_db_folder, "faiss_index.index")
path_docstore = Path.joinpath(path_vector_db_folder, "docstore.pkl")
path_index_to_docstore_id = Path.joinpath(path_vector_db_folder, "index_to_docstore_id.pkl")
if not path_vector_db_folder.exists():
    path_vector_db_folder.mkdir()
else:
    path_vector_db_folder.rmtree_p()
    path_vector_db_folder.mkdir()
for chunks in split_chunks:
    start_time = time.time()
    vector_db = FAISS.from_documents(chunks, embeddings)
    try:
        with open(str(path_docstore), 'ab') as f:
            pickle.dump(vector_db.docstore, f)
        with open(str(path_index_to_docstore_id), 'ab') as f:
            pickle.dump(vector_db.index_to_docstore_id, f)
    except:
        with open(str(path_docstore), 'wb') as f:
            pickle.dump(vector_db.docstore, f)
        with open(str(path_index_to_docstore_id), 'wb') as f:
            pickle.dump(vector_db.index_to_docstore_id, f)
    try:
        index_old = faiss.read_index(str(path_vector_db))
        index_old.add(vector_db.index)
        faiss.write_index(index_old, str(path_vector_db))
    except:
        faiss.write_index(vector_db.index, str(path_vector_db))
    finally:
        endtime = time.time()
        if (endtime - start_time) < 60:
            time.sleep(60 - (endtime - start_time))

In [101]:
chunks[0].metadata

{}

In [90]:
path_vector_db_folder,path_vector_db ,path_docstore ,path_index_to_docstore_id

(Path('VectorDatabases/ComputerOrganisation.pdf'),
 Path('VectorDatabases/ComputerOrganisation.pdf/faiss_index.index'),
 Path('VectorDatabases/ComputerOrganisation.pdf/docstore.pkl'),
 Path('VectorDatabases/ComputerOrganisation.pdf/index_to_docstore_id.pkl'))

In [1]:
loaded_faiss_index = faiss.read_index(str(path_vector_db))
# Load the docstore and index_to_docstore_id
with open(str(path_docstore), 'rb') as f:
    loaded_docstore = pickle.load(f)

with open(str(path_index_to_docstore_id), 'rb') as f:
    loaded_index_to_docstore_id = pickle.load(f)


vector_db_loaded = FAISS(
    embeddings.embed_query, 
    loaded_faiss_index, 
    loaded_docstore, 
    loaded_index_to_docstore_id
)

NameError: name 'faiss' is not defined

In [94]:
retriever = vector_db_loaded.as_retriever()

In [95]:
chunks_prompt="""
Using the Context bellow answer the question {question}, also mention the page number, name of the doc, etc relavent details at /the end of the response.

Context:
{text}
"""
RAG_prompt_template=PromptTemplate(input_variables=['text','question'],
                                    template=chunks_prompt)

In [96]:
def format_docs(docs):
    return "\n\n".join(doc.page_content for doc in docs)

In [97]:
from langchain_google_genai import ChatGoogleGenerativeAI
GEMINI_API_KEY=os.environ.get("GEMINI_API")
llm = ChatGoogleGenerativeAI(model="gemini-1.5-flash",api_key=GEMINI_API_KEY)

In [98]:
question = "Who is the author of the document?"
context = retriever.invoke(question)
rag_chain = (
    {"text": retriever | format_docs, "question": RunnablePassthrough()}
    | RAG_prompt_template
    | llm
    | StrOutputParser()
)


In [99]:
os.environ["LANGCHAIN_TRACING_V2"] = "true"
os.environ["LANGCHAIN_API_KEY"]=os.environ.get("LANGCHAIN_API")
os.environ["LANGCHAIN_ENDPOINT"]="https://api.smith.langchain.com"
os.environ["LANGCHAIN_PROJECT"]="LearnLang"
question= "What is Eight Great Ideas in Computer \
Architecture?"
rag_chain.invoke(question)

'The eight great ideas in computer architecture are:\n\n1. **Design for Moore\'s Law:** Computer architects must anticipate the rapid changes in technology driven by Moore\'s Law, which states that integrated circuit resources double every 18-24 months.  This is represented by an "up and to the right" Moore\'s Law graph.\n2. **Use Abstraction to Simplify Design:**  Abstractions are used to represent design at different levels of representation, hiding low-level details to offer a simpler model at higher levels. This is represented by an abstract painting icon.\n3. **Make the Common Case Fast:**  Optimizing the common case will enhance performance more than optimizing the rare case. This is represented by a sports car icon, as the most common trip has one or two passengers.\n4. **Performance via Parallelism:**  Performing operations in parallel is a common way to get more performance. This is represented by multiple jet engines of a plane.\n5. **Performance via Pipelining:**  A specific